In [1]:
env_dir = '/Volumes/KeithSSD/ChesapeakeMicrobiome/data/environmental_raw_data'
env_data = read.delim(paste(env_dir, 'merged_paired_water_quality_data.txt', sep="/"), sep="\t", row.names=1)

In [2]:
main_dir = '/Volumes/KeithSSD/ChesapeakeMicrobiome/data/otu_tables'
otu_table = read.delim(paste(main_dir, 'final_unrarefied_table.txt', sep="/"), sep="\t", row.names=1)
contam_df = read.delim(paste(main_dir, 'contaminant_table.txt', sep="/"), sep="\t", row.names=1)
taxa_table = read.delim(paste(main_dir, 'taxa_table_with_OTUs.txt', sep="/"), sep="\t", row.names=1)

In [4]:
# find everything that was accidentally dropped
contaminants = setdiff(colnames(contam_df), colnames(otu_table))
# match samples with environmental data
common_samples = rownames(env_data)
# subset both according to sample
contam_df2 = contam_df[common_samples, contaminants]
otu_table2 = otu_table[common_samples,]
# remove anything not present in these samples 
contam_df3 = contam_df2[,which(colSums(contam_df2) > 0)]
otu_table3 = otu_table2[,which(colSums(otu_table2) > 0)]

paste("Num shared columns", length(intersect(colnames(contam_df3), colnames(otu_table3))))
paste("Num total columns", length(union(colnames(contam_df3), colnames(otu_table3))))

# merge columns
super_Table = merge(x=contam_df3, y=otu_table3, by.x = 'row.names', by.y = 'row.names')
# drop the rownames from a copy
super_Table2 = super_Table[1:nrow(super_Table), 2:ncol(super_Table)]
# assign the rownames to their proper location
rownames(super_Table2) <- super_Table[,1]

[1] "Num shared columns 0"

[1] "Num total columns 27746"

In [5]:
outfile.1 = "/Volumes/KeithSSD/ChesapeakeMicrobiome/data/otu_tables/final_unrarefied_table.2.txt"
outfile.2 = "/Volumes/KeithSSD/ChesapeakeMicrobiome/data/otu_tables/final_rarefied_table.2.txt"
write.table(super_Table2, sep="\t", row.names=T, file=outfile.1)
colnames(super_Table2)[1:5]
rownames(super_Table2)[1:5]
dim(super_Table2)

[1] "OTU14" "OTU16" "OTU28" "OTU30" "OTU35"

[1] "95_FiltCtrl_Surface_R1"          "SB041117TAWCSCB22D11BR2TR1I288" 
[3] "SB041117TAWCSCB31D13BR1TR1I289"  "SB041117TAWCSCB32D10BR2TR1I290" 
[5] "SB041117TAWCSCB33CD24BR1TR1I291"

[1]   236 27746

In [6]:
library(phyloseq)
super_Table_ra = super_Table2 / rowSums(super_Table2)
minabund_check = which(colSums(super_Table_ra > 0.002) > 0)
OTU.clean = as.matrix(super_Table2[,minabund_check])
tax_mat = as.matrix(taxa_table)
colnames(tax_mat)[1] <- 'Domain'
tax_mat[tax_mat == ""] <- NA
tax.clean = tax_mat[colnames(OTU.clean), ]
TAX.phylo = tax_table(tax.clean)
physeq2 = phyloseq(otu_table(OTU.clean, taxa_are_rows = FALSE), TAX.phylo)

In [7]:
set.seed(42)
rare_table = rarefy_even_depth(physeq2, rngseed = 42, replace = TRUE, trimOTUs = TRUE, verbose = TRUE)

`set.seed(42)` was used to initialize repeatable random subsampling.
Please record this for your records so others can reproduce.
Try `set.seed(42); .Random.seed` for the full vector
...


In [8]:
rareOTU = as(otu_table(rare_table), "matrix")
OTUdf = as.data.frame(rareOTU)

write.table(OTUdf, sep="\t", row.names=T, file=outfile.2)
colnames(OTUdf)[1:5]
rownames(OTUdf)[1:5]
dim(OTUdf)

[1] "OTU14" "OTU16" "OTU35" "OTU39" "OTU48"

[1] "95_FiltCtrl_Surface_R1"          "SB041117TAWCSCB22D11BR2TR1I288" 
[3] "SB041117TAWCSCB31D13BR1TR1I289"  "SB041117TAWCSCB32D10BR2TR1I290" 
[5] "SB041117TAWCSCB33CD24BR1TR1I291"

[1]  236 1416

In [10]:
outfile.3 = "/Volumes/KeithSSD/ChesapeakeMicrobiome/data/otu_tables/final_rare_no_abund_filt.2.txt"
OTU.clean3 = as.matrix(super_Table2)
tax.clean3 = tax_mat[colnames(OTU.clean3), ]
TAX.phylo3 = tax_table(tax.clean3)
physeq3 = phyloseq(otu_table(OTU.clean3, taxa_are_rows = FALSE), TAX.phylo3)

set.seed(42)
rare_table2 = rarefy_even_depth(physeq3, rngseed = 42, replace = TRUE, trimOTUs = TRUE, verbose = TRUE)

rareOTU2 = as(otu_table(rare_table2), "matrix")
OTUdf2 = as.data.frame(rareOTU2)

write.table(OTUdf2, sep="\t", row.names=T, file=outfile.3)
colnames(OTUdf2)[1:5]
rownames(OTUdf2)[1:5]
dim(OTUdf2)

`set.seed(42)` was used to initialize repeatable random subsampling.
Please record this for your records so others can reproduce.
Try `set.seed(42); .Random.seed` for the full vector
...
16296OTUs were removed because they are no longer 
present in any sample after random subsampling

...


[1] "OTU14" "OTU16" "OTU28" "OTU30" "OTU35"

[1] "95_FiltCtrl_Surface_R1"          "SB041117TAWCSCB22D11BR2TR1I288" 
[3] "SB041117TAWCSCB31D13BR1TR1I289"  "SB041117TAWCSCB32D10BR2TR1I290" 
[5] "SB041117TAWCSCB33CD24BR1TR1I291"

[1]   236 11450

In [14]:
library("seqinr")
ncrna <- read.fasta(file = (paste(main_dir, 'ASV_Sequences_unfiltered.fa', sep="/")))


$names
    [1] "OTU1"     "OTU2"     "OTU3"     "OTU4"     "OTU5"     "OTU6"    
    [7] "OTU7"     "OTU8"     "OTU9"     "OTU10"    "OTU11"    "OTU12"   
   [13] "OTU13"    "OTU14"    "OTU15"    "OTU16"    "OTU17"    "OTU18"   
   [19] "OTU19"    "OTU20"    "OTU21"    "OTU22"    "OTU23"    "OTU24"   
   [25] "OTU25"    "OTU26"    "OTU27"    "OTU28"    "OTU29"    "OTU30"   
   [31] "OTU31"    "OTU32"    "OTU33"    "OTU34"    "OTU35"    "OTU36"   
   [37] "OTU37"    "OTU38"    "OTU39"    "OTU40"    "OTU41"    "OTU42"   
   [43] "OTU43"    "OTU44"    "OTU45"    "OTU46"    "OTU47"    "OTU48"   
   [49] "OTU49"    "OTU50"    "OTU51"    "OTU52"    "OTU53"    "OTU54"   
   [55] "OTU55"    "OTU56"    "OTU57"    "OTU58"    "OTU59"    "OTU60"   
   [61] "OTU61"    "OTU62"    "OTU63"    "OTU64"    "OTU65"    "OTU66"   
   [67] "OTU67"    "OTU68"    "OTU69"    "OTU70"    "OTU71"    "OTU72"   
   [73] "OTU73"    "OTU74"    "OTU75"    "OTU76"    "OTU77"    "OTU78"   
   [79] "OTU79"    "OTU80"    "OTU81"    "OTU82"    "OTU83"    "OTU84"   
   [85] "OTU85"    "OTU86"    "OTU87"    "OTU88"    "OTU89"    "OTU90"   
   [91] "OTU91"    "OTU92"    "OTU93"    "OTU94"    "OTU95"    "OTU96"   
   [97] "OTU97"    "OTU98"    "OTU99"    "OTU100"   "OTU101"   "OTU102"  
  [103] "OTU103"   "OTU104"   "OTU105"   "OTU106"   "OTU107"   "OTU108"  
  [109] "OTU109"   "OTU110"   "OTU111"   "OTU112"   "OTU113"   "OTU114"  
  [115] "OTU115"   "OTU116"   "OTU117"   "OTU118"   "OTU119"   "OTU120"  
  [121] "OTU121"   "OTU122"   "OTU123"   "OTU124"   "OTU125"   "OTU126"  
  [127] "OTU127"   "OTU128"   "OTU129"   "OTU130"   "OTU131"   "OTU132"  
  [133] "OTU133"   "OTU134"   "OTU135"   "OTU136"   "OTU137"   "OTU138"  
  [139] "OTU139"   "OTU140"   "OTU141"   "OTU142"   "OTU143"   "OTU144"  
  [145] "OTU145"   "OTU146"   "OTU147"   "OTU148"   "OTU149"   "OTU150"  
  [151] "OTU151"   "OTU152"   "OTU153"   "OTU154"   "OTU155"   "OTU156"  
  [157] "OTU157"   "OTU158"   "OTU159"   "OTU160"   "OTU161"   "OTU162"  
  [163] "OTU163"   "OTU164"   "OTU165"   "OTU166"   "OTU167"   "OTU168"  
  [169] "OTU169"   "OTU170"   "OTU171"   "OTU172"   "OTU173"   "OTU174"  
  [175] "OTU175"   "OTU176"   "OTU177"   "OTU178"   "OTU179"   "OTU180"  
  [181] "OTU181"   "OTU182"   "OTU183"   "OTU184"   "OTU185"   "OTU186"  
  [187] "OTU187"   "OTU188"   "OTU189"   "OTU190"   "OTU191"   "OTU192"  
  [193] "OTU193"   "OTU194"   "OTU195"   "OTU196"   "OTU197"   "OTU198"  
  [199] "OTU199"   "OTU200"   "OTU201"   "OTU202"   "OTU203"   "OTU204"  
  [205] "OTU205"   "OTU206"   "OTU207"   "OTU208"   "OTU209"   "OTU210"  
  [211] "OTU211"   "OTU212"   "OTU213"   "OTU214"   "OTU215"   "OTU216"  
  [217] "OTU217"   "OTU218"   "OTU219"   "OTU220"   "OTU221"   "OTU222"  
  [223] "OTU223"   "OTU224"   "OTU225"   "OTU226"   "OTU227"   "OTU228"  
  [229] "OTU229"   "OTU230"   "OTU231"   "OTU232"   "OTU233"   "OTU234"  
  [235] "OTU235"   "OTU236"   "OTU237"   "OTU238"   "OTU239"   "OTU240"  
  [241] "OTU241"   "OTU242"   "OTU243"   "OTU244"   "OTU245"   "OTU246"  
  [247] "OTU247"   "OTU248"   "OTU249"   "OTU250"   "OTU251"   "OTU252"  
  [253] "OTU253"   "OTU254"   "OTU255"   "OTU256"   "OTU257"   "OTU258"  
  [259] "OTU259"   "OTU260"   "OTU261"   "OTU262"   "OTU263"   "OTU264"  
  [265] "OTU265"   "OTU266"   "OTU267"   "OTU268"   "OTU269"   "OTU270"  
  [271] "OTU271"   "OTU272"   "OTU273"   "OTU274"   "OTU275"   "OTU276"  
  [277] "OTU277"   "OTU278"   "OTU279"   "OTU280"   "OTU281"   "OTU282"  
  [283] "OTU283"   "OTU284"   "OTU285"   "OTU286"   "OTU287"   "OTU288"  
  [289] "OTU289"   "OTU290"   "OTU291"   "OTU292"   "OTU293"   "OTU294"  
  [295] "OTU295"   "OTU296"   "OTU297"   "OTU298"   "OTU299"   "OTU300"  
  [301] "OTU301"   "OTU302"   "OTU303"   "OTU304"   "OTU305"   "OTU306"  
  [307] "OTU307"   "OTU308"   "OTU309"   "OTU310"   "OTU311"   "OTU312"  
  [313] "OTU313"   "OTU314"   "OTU315"   "OTU316"   "OTU317"   "OTU318"  
  [319] "OTU319"   "OTU320"   "OTU321"   "OTU322"   "OTU323"   "OTU324"

In [28]:
tree_dir = '/Volumes/KeithSSD/ChesapeakeMicrobiome/data/phylogenetic_tree'
treef1 = paste(tree_dir, 'query_high_abund.2.fasta', sep="/")
treef2 = paste(tree_dir, 'query_all_abund.2.fasta', sep="/")

annotation <- getAnnot(ncrna)
all_abund_bool = which(annotation %in% paste(">", names(OTUdf2), sep=""))
all_abud_both <- ncrna[all_abund_bool]
length(all_abud_both)
write.fasta(getSequence(all_abud_both), 
            sub('.', '', getAnnot(all_abud_both)), treef2)

high_abund_bool = which(annotation %in% paste(">", names(OTUdf), sep=""))
high_abud_both <- ncrna[high_abund_bool]
length(high_abud_both)
write.fasta(getSequence(high_abud_both), 
            sub('.', '', getAnnot(high_abud_both)), treef1)


[1] 11450

[1] 1416

In [29]:
test_bool = which(annotation %in% paste(">", names(OTUdf), sep=""))[1:30]
test_both <- ncrna[test_bool]
length(test_both)
write.fasta(getSequence(test_both), 
            sub('.', '', getAnnot(test_both)), 
            paste(tree_dir, 'test.2.fasta', sep="/"))


[1] 30